In [0]:
import numpy as np
from IPython.display import Audio

# Default sampling rate:
samplingrate = 44000

def db2amp(d):
    return 10 ** (float(d) / 20)
def amp2db(f):
    return 20 * np.log10(f)

def mu2s(mu_seconds):
    return mu_seconds * 1e-6
def s2mu(seconds):
    return seconds * 1e6

def ms2s(m_seconds):
    return m_seconds * 1e-3
def s2ms(seconds):
    return seconds * 1e3


def signal_energy(signal, fs=100e3):
    #signal = signal.astype(np.float64)
    #print np.min(signal), np.max(signal)
    return np.sum(signal.astype(np.float64) ** 2) / fs

def signal_power(signal, fs=100e3):
    return signal_energy(signal, fs=fs) / signal.size

def band_limits(center=8500, octave_width=1.0):
    return float(center) * 2**(-.5*octave_width), float(center) * 2**(+.5*octave_width)


def to_stereo(signal):
    """Return a tuple of left and right signal
    A single signal will be duplicated.
    A stereo signal will be returned unchanged.
    """
    try:
        signal_L, signal_R = signal
        #print "Play: Stereo"
    except ValueError:
        signal_L = signal
        signal_R = signal
        #print "Play: Mono"
    return (signal_L, signal_R)


def ramp(x = None, start = 0.0, stop = 1.0, ramp_dur = .005, fs = None, amp = 1.0):
    """ramp(x = np.ones(fs), start = .400, stop = .500, ramp_dur = .005, fs = fs, amp = 1.0)
    
    Ramp the signal x by linaer ramps between start and stop
    
    Examples
    ========
    
    >>> ramp()
    returns the default ramp function as it generates internally data x as all ones for 1 s with fs.
    """
    if fs is None:
        fs = samplingrate
    if x is None:
        x = np.ones(int(fs))
    t1 = start
    t2 = (start + ramp_dur)
    t3 = (stop - ramp_dur)
    t4 = stop
    t = np.arange(x.size) / fs
    r = amp * np.piecewise(t, [(t1 <= t) & (t < t2), (t2 <= t) & (t < t3), (t3 <= t) & (t < t4)],
                         [lambda t: (t - t1) / (t2-t1), 1, lambda t: 1 - (t - t3) / (t4-t3), 0])
    return r * x


def bandpass_itd_noise(min_freq = 20, max_freq = 20000, itd=0, fs=None, samples = None):
    """bandpass_itd_noise()
    """
    # Calculate available fft frequencies:
    if fs is None:
        fs = samplingrate
    if samples is None:
        samples = int(fs)
    freqs = np.fft.rfftfreq(samples, 1/fs)
    f = np.zeros_like(freqs)
    idx = np.where(np.logical_and(freqs>=min_freq, freqs<=max_freq))[0]
    f[idx] = 1 * np.sqrt(samples)
    f = np.array(f, dtype='complex')

    phases_rad = np.random.rand(len(f)) * 2 * np.pi
    phases = np.cos(phases_rad) + 1j * np.sin(phases_rad)

    itd_phas_rad = mu2s(itd) * np.pi * freqs #  * .5 * 2
    shift_left = np.cos(-itd_phas_rad) + 1j * np.sin(-itd_phas_rad)
    shift_right = np.cos(+itd_phas_rad) + 1j * np.sin(+itd_phas_rad)
    phases_left = phases * shift_left
    phases_right = phases * shift_right

    f_left = f * phases_left
    f_right = f * phases_right

    s_left = np.fft.irfft(f_left).real
    s_right = np.fft.irfft(f_right).real
    return s_left, s_right


def do_ild(signal, ild = 0):
    signal_L, signal_R = to_stereo(signal)
    amp_L = db2amp(-.5 * ild)
    amp_R = db2amp(+.5 * ild)
    return amp_L * signal_L, amp_R * signal_R

def noise(min_freq = 20, max_freq = 20000, itd=0, ild=0, length=1.0, autoplay=False):
    samples = int(length * samplingrate)
    signal_LR = bandpass_itd_noise(min_freq, max_freq, itd, samplingrate, samples)
    signal_LR = do_ild(signal_LR, ild)
    signal_LR = [ramp(s, start=0, stop=length) for s in signal_LR]
    display(Audio(np.vstack(signal_LR), rate=samplingrate, autoplay=autoplay))


In [0]:
print("ITD = -300 (left)")
noise(length=1, itd=-300)

print("ITD = 0 (center)")
noise(length=1, itd=0)

print("ITD = +300 (right)")
noise(length=1, itd=300)

ITD = -300 (left)


ITD = 0 (center)


ITD = +300 (right)


In [0]:
for low, high in [(20, 8000), (20, 3000), (3000, 8000)]:

  print(f"Bandwidth: {low} to {high} Hz")
  
  for itd in [-300, 0, 300]:
    print(f"ITD: {itd}")

    noise(min_freq=low, max_freq=high, itd=itd)

Bandwidth: 20 to 8000 Hz
ITD: -300


ITD: 0


ITD: 300


Bandwidth: 20 to 3000 Hz
ITD: -300


ITD: 0


ITD: 300


Bandwidth: 3000 to 8000 Hz
ITD: -300


ITD: 0


ITD: 300


In [0]:
for low, high in [(20, 8000), (20, 3000), (3000, 8000)]:

  print(f"Bandwidth: {low} to {high} Hz")
  
  for ild in [-10, 0, 10]:
    print(f"ILD: {ild}")

    noise(min_freq=low, max_freq=high, itd=0, ild=ild)

Bandwidth: 20 to 8000 Hz
ILD: -10


ILD: 0


ILD: 10


Bandwidth: 20 to 3000 Hz
ILD: -10


ILD: 0


ILD: 10


Bandwidth: 3000 to 8000 Hz
ILD: -10


ILD: 0


ILD: 10


In [0]:
sL1, sR1 = bandpass_itd_noise(min_freq =   20, max_freq=20000, itd =   0)
sL2, sR2 = bandpass_itd_noise(min_freq =   20, max_freq=20000, itd = 300)
sL2b, sR2b = bandpass_itd_noise(min_freq =   20, max_freq=20000, itd = -300)
sL3, sR3 = bandpass_itd_noise(min_freq = 4000, max_freq=20000, itd =   0)
sL4, sR4 = bandpass_itd_noise(min_freq = 4000, max_freq=20000, itd = 150)

print("Broad, center")
display(Audio(np.vstack([sL1, sR1]), rate=samplingrate))

print("Broad, right (ITD = 150)")
display(Audio(np.vstack([sL2, sR2]), rate=samplingrate))

print("Broad, center-right-left-center")
display(Audio(np.vstack([ramp(np.hstack([sL1, sL2, sL2b, sL1]), stop=4), ramp(np.hstack([sR1, sR2, sR2b, sR1]), stop=4)]), rate=samplingrate))

print("High, center")
display(Audio(np.vstack([sL3, sR3]), rate=samplingrate))

print("High, right (ITD = 150)")
display(Audio(np.vstack([sL4, sR4]), rate=samplingrate))

print("High, center-right-center")
display(Audio(np.vstack([ramp(np.hstack([sL3, sL4, sL3]), stop=3), ramp(np.hstack([sR3, sR4, sR3]), stop=3)]), rate=samplingrate))



Broad, center


Broad, right (ITD = 150)


Broad, center-right-left-center


High, center


High, right (ITD = 150)


High, center-right-center
